In [ ]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import r2_score
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Input, concatenate
from tensorflow.keras.models import Model

In [2]:
df = pd.read_csv('../dataset/dataset.csv')

df['timestamp'] = pd.to_datetime(df['timestamp'])
df['timestamp'] = df['timestamp'].dt.hour * 3600 + df['timestamp'].dt.minute * 60 + df['timestamp'].dt.second

le = LabelEncoder()
df['symbol_encoded'] = le.fit_transform(df['Symbol'])

scaler = MinMaxScaler()
df['LTP_normalized'] = scaler.fit_transform(df['LTP'].values.reshape(-1, 1))

X = df[['symbol_encoded', 'timestamp']]
y = df['LTP_normalized']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=False)


C:\Users\soham\AppData\Local\Temp\ipykernel_3448\427448392.py:5: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['timestamp'] = pd.to_datetime(df['timestamp'])


In [32]:
data = pd.read_csv('../dataset/dataset.csv')
price_data = data['LTP'].values.reshape(-1, 1)
price_data

array([[1854880],
       [1940360],
       [4398250],
       ...,
       [1934505],
       [4387275],
       [ 787290]], dtype=int64)

In [33]:
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_price_data = scaler.fit_transform(price_data)
scaled_price_data

array([[0.41646057],
       [0.43565293],
       [0.9875097 ],
       ...,
       [0.43433834],
       [0.98504554],
       [0.17676036]])

In [34]:
train_size = int(len(scaled_price_data) * 0.8)
train_data = scaled_price_data[:train_size]
test_data = scaled_price_data[train_size:]

train_data.shape
test_data.shape


(119994, 1)

In [35]:
lookback = 10  # Number of previous time steps to use for prediction
X_train, y_train = [], []
for i in range(lookback, len(train_data)):
    X_train.append(train_data[i-lookback:i, 0])
    y_train.append(train_data[i, 0])
X_train, y_train = np.array(X_train), np.array(y_train)

X_train

array([[4.16460572e-01, 4.35652934e-01, 9.87509697e-01, ...,
        3.52503618e-04, 5.57943624e-04, 2.13410630e-03],
       [4.35652934e-01, 9.87509697e-01, 1.76392137e-01, ...,
        5.57943624e-04, 2.13410630e-03, 7.86734189e-04],
       [9.87509697e-01, 1.76392137e-01, 4.20983620e-03, ...,
        2.13410630e-03, 7.86734189e-04, 2.68643681e-03],
       ...,
       [9.81172490e-04, 1.91025527e-02, 5.60750182e-03, ...,
        1.70638694e-04, 2.33730106e-02, 9.38400554e-03],
       [1.91025527e-02, 5.60750182e-03, 1.46266549e-02, ...,
        2.33730106e-02, 9.38400554e-03, 3.36786896e-05],
       [5.60750182e-03, 1.46266549e-02, 7.85836090e-06, ...,
        9.38400554e-03, 3.36786896e-05, 3.36786896e-05]])

In [36]:
X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1], 1))
X_train

array([[[4.16460572e-01],
        [4.35652934e-01],
        [9.87509697e-01],
        ...,
        [3.52503618e-04],
        [5.57943624e-04],
        [2.13410630e-03]],

       [[4.35652934e-01],
        [9.87509697e-01],
        [1.76392137e-01],
        ...,
        [5.57943624e-04],
        [2.13410630e-03],
        [7.86734189e-04]],

       [[9.87509697e-01],
        [1.76392137e-01],
        [4.20983620e-03],
        ...,
        [2.13410630e-03],
        [7.86734189e-04],
        [2.68643681e-03]],

       ...,

       [[9.81172490e-04],
        [1.91025527e-02],
        [5.60750182e-03],
        ...,
        [1.70638694e-04],
        [2.33730106e-02],
        [9.38400554e-03]],

       [[1.91025527e-02],
        [5.60750182e-03],
        [1.46266549e-02],
        ...,
        [2.33730106e-02],
        [9.38400554e-03],
        [3.36786896e-05]],

       [[5.60750182e-03],
        [1.46266549e-02],
        [7.85836090e-06],
        ...,
        [9.38400554e-03],
        [3.3678

In [37]:
lstm_input = Input(shape=(X_train.shape[1], 1), name='lstm_input')
lstm_layer = LSTM(50)(lstm_input)
dense_input = Input(shape=(1,), name='dense_input')
concat_layer = concatenate([lstm_layer, dense_input])
output_layer = Dense(1, name='output_layer')(concat_layer)
model2 = Model(inputs=[lstm_input, dense_input], outputs=output_layer)
model2.compile(optimizer='adam', loss='mean_squared_error')

In [38]:
history = model2.fit([X_train, np.zeros(X_train.shape[0])], y_train, epochs=30, batch_size=32, verbose=1)

train_loss = history.history['loss']
train_accuracy = 1 - train_loss

for i in range(len(train_accuracy)):
    print(f"Epoch {i+1} - Training Accuracy: {train_accuracy[i]}")


Epoch 1/30
14999/14999 [==============================] - 125s 8ms/step - loss: 0.0036
Epoch 2/30
14999/14999 [==============================] - 104s 7ms/step - loss: 0.0034
Epoch 3/30
14999/14999 [==============================] - 103s 7ms/step - loss: 0.0034
Epoch 4/30
14999/14999 [==============================] - 102s 7ms/step - loss: 0.0034
Epoch 5/30
14999/14999 [==============================] - 117s 8ms/step - loss: 0.0034
Epoch 6/30
14999/14999 [==============================] - 113s 8ms/step - loss: 0.0034
Epoch 7/30
14999/14999 [==============================] - 107s 7ms/step - loss: 0.0034
Epoch 8/30
14999/14999 [==============================] - 120s 8ms/step - loss: 0.0033
Epoch 9/30
14999/14999 [==============================] - 115s 8ms/step - loss: 0.0033
Epoch 10/30
14999/14999 [==============================] - 126s 8ms/step - loss: 0.0033
Epoch 11/30
14999/14999 [==============================] - 127s 8ms/step - loss: 0.0033
Epoch 12/30
14999/14999 [================

TypeError: unsupported operand type(s) for -: 'int' and 'list'

In [39]:
X_test, y_test = [], []
for i in range(lookback, len(test_data)):
    X_test.append(test_data[i-lookback:i, 0])
    y_test.append(test_data[i, 0])
X_test, y_test = np.array(X_test), np.array(y_test)

In [40]:
X_test = np.reshape(X_test, (X_test.shape[0], X_test.shape[1], 1))


In [41]:
predictions = model2.predict([X_test, np.zeros(X_test.shape[0])])


3750/3750 [==============================] - 15s 4ms/step


In [42]:
predictions = scaler.inverse_transform(predictions)
y_test = scaler.inverse_transform(y_test.reshape(-1, 1))

In [43]:
r2 = r2_score(y_test, predictions)
print("R-squared:", r2)

R-squared: 0.1606263689873466


In [46]:
for i in range(len(predictions)):
    print("Predicted:", predictions[i][0], "Actual:", y_test[i][0])

Predicted: 83937.93 Actual: 105495.0
Predicted: 98400.26 Actual: 240100.0
Predicted: 121602.01 Actual: 4175.0
Predicted: 87822.21 Actual: 375000.0
Predicted: 142478.4 Actual: 136000.0
Predicted: 113833.4 Actual: 117000.0
Predicted: 106990.34 Actual: 625.0
Predicted: 78596.02 Actual: 85000.0
Predicted: 104712.07 Actual: 152500.0
Predicted: 137707.6 Actual: 122200.0
Predicted: 137710.36 Actual: 177455.0
Predicted: 144971.97 Actual: 115000.0
Predicted: 121715.6 Actual: 5645.0
Predicted: 90529.305 Actual: 13855.0
Predicted: 83120.92 Actual: 53100.0
Predicted: 94629.36 Actual: 27095.0
Predicted: 90840.9 Actual: 181800.0
Predicted: 124201.74 Actual: 69000.0
Predicted: 107056.2 Actual: 9105.0
Predicted: 87162.33 Actual: 500.0
Predicted: 80238.89 Actual: 130.0
Predicted: 79231.13 Actual: 50.0
Predicted: 79511.8 Actual: 32000.0
Predicted: 85674.63 Actual: 85090.0
Predicted: 96369.69 Actual: 138500.0
Predicted: 106573.414 Actual: 195000.0
Predicted: 117190.81 Actual: 4675.0
Predicted: 85801.52 A